<a href="https://colab.research.google.com/github/mathew1046/encide-ml-mathew/blob/main/animalClassification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import files
files.upload()

Saving test_images.zip to test_images.zip
Saving kaggle.json to kaggle.json


{'test_images.zip': b'PK\x03\x04\x14\x00\x00\x00\x00\x00\x8e\x08\xa9Z\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x0c\x00\x00\x00test_images/PK\x03\x04\x14\x00\x00\x00\x08\x00\xf3\x9b\xa8Z\xd8\x84\x05gcU\x00\x00\xf8U\x00\x00\x18\x00\x00\x00test_images/test_001.jpg\x9c\x9aeP[_\x98\xc6\x13\x02\x04\xa7\x14)\xee\x0e\xa5\xb8\xbb\x06\x8a\x13\x1c\xfe\xc5!X\x81P\xb4P\xbc\x90\x06\tN\x8a\x04\t\xeeN)-\x94\xe2Z\xdc\x8b\xbb\x14+E\xda\xdd\xee\xce\xca\x97\xfd\xb0\xbb\xef\xfdrg\xce\x99;\xe7\x99s\x9f{\xcf\xf3\xce\xef_\x16\xfee\x1d\xf0HGS[\x13\x00\x04\x02\x00\xc0\xbf\x17\xe0_\x96\x01j\x00"0\x98\x00\x8cOD@@@LDDLF\xfb\x88\x8c\x94\x94\x8c\x89\x9a\x86\x82\x96\x83\x85\x8b\x93\x9d\x85\x9d\x8d[@\xea\x197\x9f8\x1f\x1b\xbb\xb0\x8a\x88\xb8\x8c\x9c\xa2\xa2"\x97\x90\xba\xb6\x9a<DJAQ\xee\xdf\x1e\x02$"&&#%c|\xf4\x88Q\x8e\x97\x9dW\xee\xff\\\xff\xd2\r\xa0 \x00z\x02\xaf@@v\x00\x0e\x05\x10D\x01\xfc\x97\xaf\x00\x96\xbf\xeb\xc4\x03\xfe{\x01\xfe\xa3\x808 \\<|0\x01!\x11\xf1\xdf\t-\x8f\x008@\x10\x08\x07\x17\x84\x87\x87\x8

In [2]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

In [3]:
!kaggle datasets download -d aleemaparakatta/cats-and-dogs-mini-dataset

Dataset URL: https://www.kaggle.com/datasets/aleemaparakatta/cats-and-dogs-mini-dataset
License(s): unknown


In [4]:
! unzip -q cats-and-dogs-mini-dataset.zip

In [5]:
!mkdir -p data/Cat
!mkdir -p data/Dog

!mv cats_set/* data/Cat/
!mv dogs_set/* data/Dog/

In [6]:
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
import os, shutil, random
import numpy as np
from tensorflow.keras.preprocessing import image
from tensorflow.keras.models import load_model
import pandas as pd
data_dir = 'data'
img_size = 160
batch_size = 32


In [7]:
train_gen = ImageDataGenerator(
    rescale=1./255,
    validation_split=0.2,
    horizontal_flip=True,
    rotation_range=20,
    zoom_range=0.2
)

train_data = train_gen.flow_from_directory(
    data_dir,
    target_size=(img_size, img_size),
    batch_size=batch_size,
    class_mode='binary',
    subset='training'
)

val_data = train_gen.flow_from_directory(
    data_dir,
    target_size=(img_size, img_size),
    batch_size=batch_size,
    class_mode='binary',
    subset='validation'
)


Found 800 images belonging to 2 classes.
Found 200 images belonging to 2 classes.


In [8]:
!rm -rf data/.ipynb_checkpoints

In [9]:
base_model = tf.keras.applications.MobileNetV2(
    input_shape=(img_size, img_size, 3),
    include_top=False,
    weights='imagenet'
)
base_model.trainable = False

9406464/9406464 ━━━━━━━━━━━━━━━━━━━━ 0s 0us/step


In [10]:
model = tf.keras.Sequential([
    base_model,
    tf.keras.layers.GlobalAveragePooling2D(),
    tf.keras.layers.Dense(1, activation='sigmoid')
])

In [11]:
model.compile(
    optimizer='adam',
    loss='binary_crossentropy',
    metrics=['accuracy']
)

history = model.fit(
    train_data,
    validation_data=val_data,
    epochs=5
)

/usr/local/lib/python3.11/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


Epoch 1/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 30s 1s/step - accuracy: 0.6956 - loss: 0.5709 - val_accuracy: 0.9050 - val_loss: 0.2649
Epoch 2/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 39s 926ms/step - accuracy: 0.9291 - loss: 0.1859 - val_accuracy: 0.9200 - val_loss: 0.2216
Epoch 3/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 23s 904ms/step - accuracy: 0.9436 - loss: 0.1416 - val_accuracy: 0.9400 - val_loss: 0.1906
Epoch 4/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 23s 910ms/step - accuracy: 0.9555 - loss: 0.1135 - val_accuracy: 0.9450 - val_loss: 0.1804
Epoch 5/5
25/25 ━━━━━━━━━━━━━━━━━━━━ 41s 921ms/step - accuracy: 0.9726 - loss: 0.1017 - val_accuracy: 0.9550 - val_loss: 0.1575


In [12]:
model.save('model.h5')

In [13]:
acc = history.history['accuracy']
print(f"Final Training Accuracy: {acc[-1]:.4f}")

Final Training Accuracy: 0.9650


In [16]:
!unzip -q test_images.zip

In [17]:
test_dir = 'test_images'
img_size = (160, 160)
for filename in sorted(os.listdir(test_dir)):
    if filename.lower().endswith(('.jpg', '.png', '.jpeg')):
        img_path = os.path.join(test_dir, filename)
        img = image.load_img(img_path, target_size=img_size)
        img_array = image.img_to_array(img)
        img_array = np.expand_dims(img_array, axis=0) / 255.0  # Normalize

        pred = model.predict(img_array)[0][0]
        label = "Dog" if pred > 0.5 else "Cat"
        print(f"{filename}: {label} (Confidence: {pred:.4f})")


1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step
test_001.jpg: Cat (Confidence: 0.0097)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
test_002.jpg: Cat (Confidence: 0.0286)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
test_003.jpg: Cat (Confidence: 0.0045)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
test_004.jpg: Cat (Confidence: 0.0843)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 60ms/step
test_005.jpg: Cat (Confidence: 0.0132)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
test_006.jpg: Cat (Confidence: 0.0593)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step
test_007.jpg: Cat (Confidence: 0.0601)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
test_008.jpg: Cat (Confidence: 0.0009)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
test_009.jpg: Cat (Confidence: 0.0014)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
test_010.jpg: Cat (Confidence: 0.1572)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
test_011.jpg: Cat (Confidence: 0.0507)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
test_012.jpg: Cat (Confidence: 0.0005)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
test_013.jpg: Cat (Confidence: 0.0484)
1